In [1]:
### 形態素解析
import MeCab

#text = "私はお昼休みに美味しいカレーライスを食べました。"

m = MeCab.Tagger("-Ochasen")

def mecab_sep(text):
    node = m.parseToNode(text)

    words_list = []

    while node:
        if node.feature.split(",")[0] == "動詞":
            words_list.append(node.feature.split(",")[6])
        elif node.feature.split(",")[0] == "形容詞":
            words_list.append(node.feature.split(",")[6])
        else:
            words_list.append(node.surface)

        node = node.next
        
    return words_list[1:-1]

In [4]:
from gensim.models.doc2vec import Doc2Vec
model = Doc2Vec.load("jawiki.doc2vec.dbow300d/jawiki.doc2vec.dbow300d.model")


In [5]:
def calc_vecs_d2v(docs):
    vecs = []
    for d in docs:
        vecs.append(model.infer_vector(mecab_sep(d)))
    
    return vecs

In [6]:
### Bag-of-words / tf-idf
from sklearn.feature_extraction.text import TfidfVectorizer

def calc_vecs(docs):
    vectorizer = TfidfVectorizer(analyzer=mecab_sep)
    vecs = vectorizer.fit_transform(docs)
    return vecs.toarray()


In [15]:
### コサイン類似度
import numpy as np
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity

input_doc = "君はネコが好きです。"

target_docs_df = pd.read_csv("target_docs.csv")
target_docs = target_docs_df["文章リスト"].tolist()

all_docs = [input_doc] + target_docs
all_docs_vecs = calc_vecs_d2v(all_docs)

similarity =cosine_similarity([all_docs_vecs[0]],all_docs_vecs[1:])

target_docs_df["類似度"] = similarity[0]

In [14]:
target_docs_df.sort_values("類似度",ascending=False)

文章リスト       類似度
0      私は犬が好きです。  0.438497
4    あなたは猫が好きです。  0.388658
2   私は犬がとても好きです。  0.354345
3  あなたは犬と猫が好きです。  0.310741
1      私は犬が嫌いです。  0.278822

In [16]:
target_docs_df.sort_values("類似度",ascending=False)

文章リスト       類似度
4    あなたは猫が好きです。  0.924543
3  あなたは犬と猫が好きです。  0.919218
0      私は犬が好きです。  0.907596
1      私は犬が嫌いです。  0.903666
2   私は犬がとても好きです。  0.902655

In [7]:
import glob
target_docs=[]

for x in glob.glob("text/*/*.txt"):
    text = ""
    with open(x) as f:
        next(f)
        next(f)
        for line in f:
            text = text + line
    f.close()
    target_docs.append(text)


カテゴリ                                                 内容
0     movie-enter  【DVDエンター！】誘拐犯に育てられた女が目にした真実は、孤独か幸福か\n　2005年11月...
1     movie-enter  藤原竜也、中学生とともにロケット打ち上げに成功\n　「アンテナを張りながら生活をしていけばい...
2     movie-enter  『戦火の馬』ロイヤル・プレミアにウィリアム王子＆キャサリン妃が出席\n　3月2日より全国ロー...
3     movie-enter  香里奈、女子高生100人のガチンコ質問に回答「ラーメンも食べる」\n　女優の香里奈が18日、...
4     movie-enter  ユージの前に立ちはだかったJOY「僕はAKBの高橋みなみを守る」\n　5日、東京・千代田区の...
...           ...                                                ...
7371         smax  好きな戦士を作ってドラゴンボールの世界で天下一武道会優勝だ！「挑戦！天下一武道会」【Andr...
7372         smax  NTTドコモ、GALAXY SIII SC-06DとF-09D ANTEPRIMAの発売日を...
7373         smax  NTTドコモ、Android向け「docomo Wi-Fiかんたん接続アプリ」をバージョンア...
7374         smax  NTTドコモ、PRADA Phone by LG L-02Dのデコメ絵文字popが正常に表示...
7375         smax  NTTドコモ、公式オンラインショップでも端末複数台購入で最大10,500円／台の割り引きが受...

[7376 rows x 2 columns]

In [8]:
all_docs_vecs = calc_vecs_d2v(target_docs)

In [35]:
### コサイン類似度
import numpy as np
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity

input_doc = "お前らどんだけ起きてんだよ！"

similarity =cosine_similarity(calc_vecs_d2v([input_doc]),all_docs_vecs)

target_docs_df = pd.DataFrame(target_docs,columns=["文章リスト"])
target_docs_df["類似度"] = similarity[0]

In [38]:
target_docs_df.sort_values("類似度",ascending=False).head(5)["文章リスト"].tolist()[1]

'ツイッターでストレス発散？\u3000ローラが老人の弁当のおかずを聞かれ「もちーo(^u^)o」【話題】\nツイッターが人気のタレントと言えば思い出すのがローラ。そんな彼女がまた仰天発言を行った。\nファンからの「ローラ明日おばあちゃんのゲートボール大会あるんだけどおかず何がいいと思う？」というツイートに対するローラの返事は「もちーo(^u^)o」だったのだ。\n\nおばあちゃんにお餅！\u3000と思ってしまったが、ネット上でも「おばあちゃん危ない」「見た瞬間爆笑した」などの声があがっている。ローラの返事を面白がっている人が多いのだが、中には「ツイッターでストレス発散してるのかな」などの書き込みもあった。\n\nどうも気になるローラのツイッター。目が離せない。\n\n＠ローラツイッター\n'